In [20]:
import pandas as pd
import glob
import os
import psycopg2
from sqlalchemy import create_engine
import time
import frictionless
import numpy as np

In [2]:
B_NAME = 'dadosmg'
DATASETS_DIR = 'despesa/'
DATASET_DIR = 'datasets/'
DATA_DIR = 'data/'
DATA_PATH = DATASET_DIR + DATASETS_DIR + DATA_DIR

# obtem lista de paths para arquivos CSV localizados no caminho DATA_PATH
file_paths = [i.replace('\\', '/') for i in list(glob.iglob(f'{DATA_PATH}*.csv*'))]

# paths de bases csv que sao separadas por anos
file_paths_desp = [x for x in file_paths if "dm_empenho_desp_" in x]
file_paths_ft = [x for x in file_paths if "ft_despesa_" in x]

# paths de bases csv que não são separadas por anos
file_paths = list(set(file_paths) - set(file_paths_desp) - set(file_paths_ft))

# True Dropa todas as tabelas atuais da database
DROP_TABLES = True

package = frictionless.Package('datasets/despesa/data/datapackage.json')

In [3]:
import sqlalchemy

TYPES = {
    'string': {
        'default': sqlalchemy.types.String,
        'binary': sqlalchemy.types.LargeBinary
    },
    'number': {
        'default': sqlalchemy.types.Numeric
    },
    'integer': {
        'default': sqlalchemy.types.Integer
    },
    'boolean': {
        'default': sqlalchemy.types.Boolean
    },
    'null': {
        'default': sqlalchemy.types.NullType
    },
    'object': {
        'default': None
    },
    'datetime': {
        'default': sqlalchemy.types.DateTime
    },
    'date': {
        'default': sqlalchemy.types.Date
    },
    'time': {
        'default': sqlalchemy.types.Time
    },
    'geopoint': {
        'default': None
    },
    'geojson': {
        'default': None
    },
    'any': {
        'default': None
    }
}

def get_column_type(field):
    type_ = field.get('type')
    format_ = field.get('format', 'default')
    formats = TYPES.get(type_, {})
    return formats.get(format_) or formats.get('default')

In [31]:
FRICT_TO_DTYPES = {
    'string': object
    ,
    'number': np.float64
    ,
    'integer': np.int64
    ,
    'boolean': bool
    ,
    'null': None
    ,
    'object': object
    ,
    'datetime': np.datetime64[ns]
    ,
    'date': np.datetime64
    ,
    'time': np.datetime64
    ,
    'geopoint': object
    ,
    'geojson': object
    ,
    'any': object
}




In [75]:
package.resources

[{'name': 'dm_unidade_orc',
  'type': 'table',
  'title': 'Unidade Orçamentária',
  'profile': 'tabular-data-resource',
  'sources': [{'title': 'Tabela origem no schema AGE7 no banco de dados do '
                        'Portal da Transparência',
               'table': 'dm_unidade_orc'}],
  'path': 'data/dm_unidade_orc.csv.gz',
  'scheme': 'file',
  'format': 'csv',
  'mediatype': 'text/csv',
  'compression': 'gz',
  'encoding': 'utf-8-sig',
  'dialect': {'csv': {'delimiter': ';',
                      'lineTerminator': '\r\n',
                      'quoteChar': '"',
                      'doubleQuote': True,
                      'skipInitialSpace': False}},
  'schema': {'fields': [{'name': 'id_unidade_orc',
                         'type': 'integer',
                         'title': 'Unidade Orçamentária - Chave',
                         'format': 'default',
                         'constraints': {'required': True, 'unique': False},
                         'bareNumber': True},


In [83]:
schema = package.get_resource('dm_empenho_desp_2002').name
schema

'dm_empenho_desp_2002'

In [67]:
schema = package.resources[8].schema
print(package.resources[8].name)

for field in schema.fields:
    print(f'-> {field.name} - {field.type}')
    print(FRICT_TO_DTYPES.get(field.type ))

dm_empenho_desp_2002
-> id_empenho - integer
<class 'numpy.int64'>
-> ano_exercicio - year
None
-> nr_empenho - string
<class 'object'>
-> dt_empenho - date
<class 'numpy.datetime64'>
-> unidade_executora - string
<class 'object'>
-> tipo_empenho - string
<class 'object'>
-> vr_empenho - number
<class 'numpy.float64'>
-> cd_uni_prog_gasto - integer
<class 'numpy.int64'>
-> uni_prog_gasto - string
<class 'object'>


In [68]:
dtypes_dict = {field.name:FRICT_TO_DTYPES.get(field.type) for field in schema.fields}
dtypes_dict

{'id_empenho': numpy.int64,
 'ano_exercicio': None,
 'nr_empenho': object,
 'dt_empenho': numpy.datetime64,
 'unidade_executora': object,
 'tipo_empenho': object,
 'vr_empenho': numpy.float64,
 'cd_uni_prog_gasto': numpy.int64,
 'uni_prog_gasto': object}

In [69]:
df = pd.read_csv('datasets/despesa/data/dm_empenho_desp_2002.csv.gz', delimiter=';', decimal='.')
df.dtypes

id_empenho             int64
ano_exercicio          int64
nr_empenho             int64
dt_empenho            object
unidade_executora     object
tipo_empenho          object
vr_empenho           float64
cd_uni_prog_gasto      int64
uni_prog_gasto       float64
dtype: object

In [70]:
df

id_empenho  ano_exercicio  nr_empenho  dt_empenho  \
0           788991           2002          27  2002-01-24   
1           789106           2002           5  2002-01-29   
2           789107           2002          24  2002-01-29   
3           789108           2002          26  2002-01-29   
4           789109           2002           2  2002-01-29   
...            ...            ...         ...         ...   
606145    10003467           2002         146  2002-12-30   
606146    10003468           2002         162  2002-12-30   
606147    10003469           2002         926  2002-12-30   
606148    10003470           2002        1824  2002-12-30   
606149    10003471           2002        1994  2002-12-30   

                         unidade_executora tipo_empenho  vr_empenho  \
0         1030001 - TRIBUNAL DE JUSTICA MG     ESTIMADO       97.46   
1                            2180001 - FCS     ESTIMADO      492.62   
2                          2080001 - CETEC    ORDINÁRIO      388.15   
3                          2080001 - CETEC     ESTIMADO     5026.49   
4         1260064 - SEE - SUP. DE FINANCAS    ORDINÁRIO      200.00   
...                                    ...          ...         ...   
606145                      5200001 - BDMG    ORDINÁRIO   650000.00   
606146                      5200001 - BDMG    ORDINÁRIO   117063.37   
606147                      2170001 - FAOP     ESTIMADO      450.00   
606148    1320010 - SES-SUP. EPIDEMIOLOGIA    ORDINÁRIO     1100.00   
606149  2270004 - FHEMIG-C.GERAL PEDIATRIA     ESTIMADO    57000.00   

        cd_uni_prog_gasto  uni_prog_gasto  
0                       0             NaN  
1                       0             NaN  
2                       0             NaN  
3                       0             NaN  
4                     317             NaN  
...                   ...             ...  
606145                  0             NaN  
606146                  0             NaN  
606147                  0             NaN  
606148                  0             NaN  
606149                  0             NaN  

[606150 rows x 9 columns]

In [77]:
df = df.astype(dtypes_dict)
print(df.dtypes)


id_empenho                    int64
ano_exercicio                 int64
nr_empenho                   object
dt_empenho           datetime64[ns]
unidade_executora            object
tipo_empenho                 object
vr_empenho                  float64
cd_uni_prog_gasto             int64
uni_prog_gasto               object
dtype: object
None


C:\Users\andre\AppData\Local\Temp\ipykernel_24356\2470052345.py:1: FutureWarning: Passing unit-less datetime64 dtype to .astype is deprecated and will raise in a future version. Pass 'datetime64[ns]' instead
  df = df.astype(dtypes_dict)


In [78]:
df


id_empenho  ano_exercicio nr_empenho dt_empenho  \
0           788991           2002         27 2002-01-24   
1           789106           2002          5 2002-01-29   
2           789107           2002         24 2002-01-29   
3           789108           2002         26 2002-01-29   
4           789109           2002          2 2002-01-29   
...            ...            ...        ...        ...   
606145    10003467           2002        146 2002-12-30   
606146    10003468           2002        162 2002-12-30   
606147    10003469           2002        926 2002-12-30   
606148    10003470           2002       1824 2002-12-30   
606149    10003471           2002       1994 2002-12-30   

                         unidade_executora tipo_empenho  vr_empenho  \
0         1030001 - TRIBUNAL DE JUSTICA MG     ESTIMADO       97.46   
1                            2180001 - FCS     ESTIMADO      492.62   
2                          2080001 - CETEC    ORDINÁRIO      388.15   
3                          2080001 - CETEC     ESTIMADO     5026.49   
4         1260064 - SEE - SUP. DE FINANCAS    ORDINÁRIO      200.00   
...                                    ...          ...         ...   
606145                      5200001 - BDMG    ORDINÁRIO   650000.00   
606146                      5200001 - BDMG    ORDINÁRIO   117063.37   
606147                      2170001 - FAOP     ESTIMADO      450.00   
606148    1320010 - SES-SUP. EPIDEMIOLOGIA    ORDINÁRIO     1100.00   
606149  2270004 - FHEMIG-C.GERAL PEDIATRIA     ESTIMADO    57000.00   

        cd_uni_prog_gasto uni_prog_gasto  
0                       0            NaN  
1                       0            NaN  
2                       0            NaN  
3                       0            NaN  
4                     317            NaN  
...                   ...            ...  
606145                  0            NaN  
606146                  0            NaN  
606147                  0            NaN  
606148                  0            NaN  
606149                  0            NaN  

[606150 rows x 9 columns]

In [106]:
path1 = os.path.normpath(package.get_resource('dm_unidade_orc').basepath)
path2 = os.path.normpath(package.get_resource('dm_unidade_orc').path)
path1_folders = path1.split('/')
path2_folders = path2.split('/')
common_folders = [folder for folder in path1_folders if folder in path2_folders]
for folder in common_folders:
    print(folder)
    path2_folders.remove(folder)
new_path = os.path.join(path1, *path2_folders)
new_path

'datasets\\despesa\\data\\data\\dm_unidade_orc.csv.gz'

In [109]:
resources_desp = [package.get_resource(x) for x in package.resource_names if "dm_empenho_desp_" in x]
resources_ft = [package.get_resource(x) for x in package.resource_names if "ft_despesa_" in x]

In [113]:
for resource in resources_desp:
    print (resource.name)

dm_empenho_desp_2002
dm_empenho_desp_2003
dm_empenho_desp_2004
dm_empenho_desp_2005
dm_empenho_desp_2006
dm_empenho_desp_2007
dm_empenho_desp_2008
dm_empenho_desp_2009
dm_empenho_desp_2010
dm_empenho_desp_2011
dm_empenho_desp_2012
dm_empenho_desp_2013
dm_empenho_desp_2014
dm_empenho_desp_2015
dm_empenho_desp_2016
dm_empenho_desp_2017
dm_empenho_desp_2018
dm_empenho_desp_2019
dm_empenho_desp_2020
dm_empenho_desp_2021
dm_empenho_desp_2022
dm_empenho_desp_2023
